<a href="https://colab.research.google.com/github/AnanyaTyagi/VAE-GAN-Diffusion-Benchmark/blob/main/Diffusion.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# --- GPU + Drive ---
!nvidia-smi -L || true

from google.colab import drive
import os, random, json, math, time
import numpy as np
drive_ok = True
try:
    drive.mount('/content/drive', force_remount=True)
    OUT_DIR = "/content/drive/MyDrive/diffusion_cifar10_runs"   # change if you like
    print("✅ Drive mounted. Saving to:", OUT_DIR)
except Exception as e:
    print("⚠️ Drive mount failed, saving locally. Error:", e)
    OUT_DIR = "/content/diffusion_cifar10_runs"
    drive_ok = False
os.makedirs(OUT_DIR, exist_ok=True)

# --- Repro/Device ---
import torch
device = "cuda" if torch.cuda.is_available() else "cpu"
torch.backends.cudnn.benchmark = True

def set_seed(seed=42):
    random.seed(seed); np.random.seed(seed)
    torch.manual_seed(seed); torch.cuda.manual_seed_all(seed)
set_seed(42)

# --- Small helpers ---
from torchvision.utils import save_image, make_grid
def denorm(x):                      # [-1,1] -> [0,1]
    return (x.clamp(-1,1) + 1)/2

print("Device:", device)
print("OUT_DIR:", OUT_DIR)

GPU 0: NVIDIA A100-SXM4-40GB (UUID: GPU-29cddfd2-c2c2-cad2-0513-e7e669543a90)
Mounted at /content/drive
✅ Drive mounted. Saving to: /content/drive/MyDrive/diffusion_cifar10_runs
Device: cuda
OUT_DIR: /content/drive/MyDrive/diffusion_cifar10_runs


In [ ]:
# ============================================================
# IMPROVED DIFFUSION ON CIFAR-10: TRAIN + 10K SAMPLES + FID/IS/KID
# ============================================================

# --- GPU + Drive ---
!nvidia-smi -L || true

from google.colab import drive
import os, random, json, math, time
import numpy as np

drive_ok = True
try:
    drive.mount('/content/drive', force_remount=True)
    OUT_DIR = "/content/drive/MyDrive/diffusion_cifar10_runs"
    print("✅ Drive mounted. Saving to:", OUT_DIR)
except Exception as e:
    print("⚠️ Drive mount failed, saving locally. Error:", e)
    OUT_DIR = "/content/diffusion_cifar10_runs"
    drive_ok = False

os.makedirs(OUT_DIR, exist_ok=True)

# --- Repro/Device ---
import torch
import torch.nn as nn
import torch.nn.functional as F

device = "cuda" if torch.cuda.is_available() else "cpu"
torch.backends.cudnn.benchmark = True

def set_seed(seed=42):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    if torch.cuda.is_available():
        torch.cuda.manual_seed_all(seed)

set_seed(42)

from torchvision import datasets, transforms
from torch.utils.data import DataLoader
from torchvision.utils import save_image, make_grid
from tqdm.auto import tqdm

def denorm(x):
    return (x.clamp(-1,1) + 1)/2

print("Device:", device)
print("OUT_DIR:", OUT_DIR)


# -------------------------
# IMPROVED MODEL COMPONENTS
# -------------------------

class SinusoidalPosEmb(nn.Module):
    def __init__(self, dim):
        super().__init__()
        self.dim = dim

    def forward(self, t):
        device_ = t.device
        half = self.dim // 2
        emb_factor = math.log(10000) / (half - 1)
        emb = torch.exp(torch.arange(half, device=device_) * -emb_factor)
        emb = t[:, None] * emb[None, :]
        emb = torch.cat([torch.sin(emb), torch.cos(emb)], dim=-1)
        return emb


def get_num_groups(channels):
    """Helper function to get valid num_groups for GroupNorm"""
    if channels >= 32:
        num_groups = 8
    elif channels >= 16:
        num_groups = 4
    elif channels >= 8:
        num_groups = 2
    else:
        num_groups = 1

    # Ensure divisibility
    while channels % num_groups != 0:
        num_groups -= 1
    return max(1, num_groups)


class SelfAttention(nn.Module):
    """Multi-head self-attention for spatial features"""
    def __init__(self, channels, num_heads=4):
        super().__init__()
        self.channels = channels
        self.num_heads = num_heads

        # Adjust num_heads if channels is too small
        while channels % num_heads != 0 and num_heads > 1:
            num_heads -= 1
        self.num_heads = num_heads

        self.norm = nn.GroupNorm(get_num_groups(channels), channels)
        self.qkv = nn.Conv2d(channels, channels * 3, 1)
        self.proj = nn.Conv2d(channels, channels, 1)

    def forward(self, x):
        B, C, H, W = x.shape

        qkv = self.qkv(self.norm(x))
        q, k, v = qkv.chunk(3, dim=1)

        # Reshape for multi-head attention
        q = q.view(B, self.num_heads, C // self.num_heads, H * W)
        k = k.view(B, self.num_heads, C // self.num_heads, H * W)
        v = v.view(B, self.num_heads, C // self.num_heads, H * W)

        # Attention
        scale = (C // self.num_heads) ** -0.5
        attn = torch.softmax(torch.einsum('bhcn,bhcm->bhnm', q, k) * scale, dim=-1)
        out = torch.einsum('bhnm,bhcm->bhcn', attn, v)

        out = out.reshape(B, C, H, W)
        return x + self.proj(out)


class ResBlock(nn.Module):
    def __init__(self, in_ch, out_ch, time_dim, dropout=0.1):
        super().__init__()

        self.time_mlp = nn.Sequential(
            nn.SiLU(),
            nn.Linear(time_dim, out_ch)
        )

        self.block1 = nn.Sequential(
            nn.GroupNorm(get_num_groups(in_ch), in_ch),
            nn.SiLU(),
            nn.Conv2d(in_ch, out_ch, 3, padding=1),
        )

        self.block2 = nn.Sequential(
            nn.GroupNorm(get_num_groups(out_ch), out_ch),
            nn.SiLU(),
            nn.Dropout(dropout),
            nn.Conv2d(out_ch, out_ch, 3, padding=1),
        )

        self.res_conv = nn.Conv2d(in_ch, out_ch, 1) if in_ch != out_ch else nn.Identity()

    def forward(self, x, t_emb):
        h = self.block1(x)

        t = self.time_mlp(t_emb)[:, :, None, None]
        h = h + t

        h = self.block2(h)
        return h + self.res_conv(x)


class UNet(nn.Module):
    """
    Improved UNet with attention and more capacity
    Architecture: 32x32 -> 16x16 -> 8x8 (bottleneck) -> 16x16 -> 32x32
    """
    def __init__(self, img_ch=3, base_channels=128, time_dim=256, dropout=0.1):
        super().__init__()

        self.time_mlp = nn.Sequential(
            SinusoidalPosEmb(time_dim),
            nn.Linear(time_dim, time_dim * 4),
            nn.SiLU(),
            nn.Linear(time_dim * 4, time_dim),
        )

        ch1 = base_channels        # 128
        ch2 = base_channels * 2    # 256
        ch3 = base_channels * 4    # 512

        # ---- Encoder ----
        # 32x32 -> 32x32 (ch1)
        self.down1 = nn.ModuleList([
            ResBlock(img_ch, ch1, time_dim, dropout),
            ResBlock(ch1, ch1, time_dim, dropout),
        ])

        # 16x16 -> 16x16 (ch2)
        self.down2 = nn.ModuleList([
            ResBlock(ch1, ch2, time_dim, dropout),
            ResBlock(ch2, ch2, time_dim, dropout),
        ])
        self.attn2 = SelfAttention(ch2, num_heads=4)

        # 8x8 -> 8x8 (ch3)
        self.down3 = nn.ModuleList([
            ResBlock(ch2, ch3, time_dim, dropout),
            ResBlock(ch3, ch3, time_dim, dropout),
        ])
        self.attn3 = SelfAttention(ch3, num_heads=4)

        self.pool = nn.AvgPool2d(2)

        # ---- Bottleneck (at 8x8, ch3) ----
        self.mid1 = ResBlock(ch3, ch3, time_dim, dropout)
        self.mid_attn = SelfAttention(ch3, num_heads=4)
        self.mid2 = ResBlock(ch3, ch3, time_dim, dropout)

        # ---- Decoder ----
        # 8x8 upsampled to 16x16, then concat with d2 (16x16, ch2)
        self.up2 = nn.ModuleList([
            ResBlock(ch3 + ch2, ch2, time_dim, dropout),
            ResBlock(ch2, ch2, time_dim, dropout),
        ])
        self.attn_up2 = SelfAttention(ch2, num_heads=4)

        # 16x16 upsampled to 32x32, then concat with d1 (32x32, ch1)
        self.up1 = nn.ModuleList([
            ResBlock(ch2 + ch1, ch1, time_dim, dropout),
            ResBlock(ch1, ch1, time_dim, dropout),
        ])
        self.attn_up1 = SelfAttention(ch1, num_heads=4)

        self.upsample = nn.Upsample(scale_factor=2, mode="nearest")

        self.final = nn.Sequential(
            nn.GroupNorm(get_num_groups(ch1), ch1),
            nn.SiLU(),
            nn.Conv2d(ch1, img_ch, 3, padding=1),
        )

    def forward(self, x, t):
        t_emb = self.time_mlp(t)

        # Encoder
        # Level 1: 32x32
        h = x
        for block in self.down1:
            h = block(h, t_emb)
        d1 = h  # Save for skip connection (32x32, ch1)

        # Level 2: 16x16
        h = self.pool(h)
        for block in self.down2:
            h = block(h, t_emb)
        h = self.attn2(h)
        d2 = h  # Save for skip connection (16x16, ch2)

        # Level 3: 8x8
        h = self.pool(h)
        for block in self.down3:
            h = block(h, t_emb)
        h = self.attn3(h)  # (8x8, ch3)

        # Bottleneck (8x8, ch3)
        h = self.mid1(h, t_emb)
        h = self.mid_attn(h)
        h = self.mid2(h, t_emb)

        # Decoder
        # 8x8 -> 16x16
        h = self.upsample(h)  # (16x16, ch3)
        h = torch.cat([h, d2], dim=1)  # (16x16, ch3+ch2)
        for block in self.up2:
            h = block(h, t_emb)
        h = self.attn_up2(h)  # (16x16, ch2)

        # 16x16 -> 32x32
        h = self.upsample(h)  # (32x32, ch2)
        h = torch.cat([h, d1], dim=1)  # (32x32, ch2+ch1)
        for block in self.up1:
            h = block(h, t_emb)
        h = self.attn_up1(h)  # (32x32, ch1)

        return self.final(h)


# -------------------------
# IMPROVED DIFFUSION SCHEDULE (Cosine)
# -------------------------

T = 1000

def cosine_beta_schedule(timesteps, s=0.008):
    """
    Cosine schedule as proposed in https://arxiv.org/abs/2102.09672
    """
    steps = timesteps + 1
    x = torch.linspace(0, timesteps, steps)
    alphas_cumprod = torch.cos(((x / timesteps) + s) / (1 + s) * math.pi * 0.5) ** 2
    alphas_cumprod = alphas_cumprod / alphas_cumprod[0]
    betas = 1 - (alphas_cumprod[1:] / alphas_cumprod[:-1])
    return torch.clip(betas, 0.0001, 0.9999)

betas = cosine_beta_schedule(T)

alphas = 1.0 - betas
alphas_cumprod = torch.cumprod(alphas, dim=0)
alphas_cumprod_prev = torch.cat(
    [torch.tensor([1.0], dtype=torch.float32), alphas_cumprod[:-1]], dim=0
)

sqrt_alphas_cumprod = torch.sqrt(alphas_cumprod)
sqrt_one_minus_alphas_cumprod = torch.sqrt(1.0 - alphas_cumprod)
sqrt_recip_alphas = torch.sqrt(1.0 / alphas)
posterior_variance = betas * (1.0 - alphas_cumprod_prev) / (1.0 - alphas_cumprod)

# Move to device
betas = betas.to(device)
alphas = alphas.to(device)
alphas_cumprod = alphas_cumprod.to(device)
alphas_cumprod_prev = alphas_cumprod_prev.to(device)
sqrt_alphas_cumprod = sqrt_alphas_cumprod.to(device)
sqrt_one_minus_alphas_cumprod = sqrt_one_minus_alphas_cumprod.to(device)
sqrt_recip_alphas = sqrt_recip_alphas.to(device)
posterior_variance = posterior_variance.to(device)


def q_sample(x0, t, noise=None):
    if noise is None:
        noise = torch.randn_like(x0)
    sqrt_alpha_bar_t = sqrt_alphas_cumprod[t][:, None, None, None]
    sqrt_one_minus_alpha_bar_t = sqrt_one_minus_alphas_cumprod[t][:, None, None, None]
    return sqrt_alpha_bar_t * x0 + sqrt_one_minus_alpha_bar_t * noise


def diffusion_loss(model, x0):
    B = x0.size(0)
    t = torch.randint(0, T, (B,), device=device, dtype=torch.long)
    noise = torch.randn_like(x0)
    x_t = q_sample(x0, t, noise)
    eps_pred = model(x_t, t)
    return F.mse_loss(eps_pred, noise)


# -------------------------
# EMA Helper
# -------------------------

class EMA:
    def __init__(self, model, decay=0.9999):
        self.model = model
        self.decay = decay
        self.shadow = {}
        self.backup = {}

        for name, param in model.named_parameters():
            if param.requires_grad:
                self.shadow[name] = param.data.clone()

    def update(self):
        for name, param in self.model.named_parameters():
            if param.requires_grad:
                self.shadow[name].mul_(self.decay).add_(param.data, alpha=1 - self.decay)

    def apply_shadow(self):
        for name, param in self.model.named_parameters():
            if param.requires_grad:
                self.backup[name] = param.data.clone()
                param.data.copy_(self.shadow[name])

    def restore(self):
        for name, param in self.model.named_parameters():
            if param.requires_grad:
                param.data.copy_(self.backup[name])
        self.backup = {}


# -------------------------
# CIFAR-10 DATALOADER with augmentation
# -------------------------

BATCH_SIZE = 64

transform = transforms.Compose([
    transforms.RandomHorizontalFlip(),
    transforms.ToTensor(),
    transforms.Normalize((0.5,0.5,0.5),(0.5,0.5,0.5)),
])

trainset = datasets.CIFAR10("./data", train=True, download=True, transform=transform)
trainloader = DataLoader(trainset, batch_size=BATCH_SIZE, shuffle=True,
                         num_workers=2, pin_memory=True, drop_last=True)

print("Train batches:", len(trainloader))


# -------------------------
# TRAINING LOOP
# -------------------------

EPOCHS = 500
LR = 2e-4

model = UNet(img_ch=3, base_channels=128, time_dim=256, dropout=0.1).to(device)
optimizer = torch.optim.AdamW(model.parameters(), lr=LR, weight_decay=0.0)
ema = EMA(model, decay=0.9999)

scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=EPOCHS, eta_min=1e-6)

def p_sample(model, x, t_index: int):
    b = x.size(0)
    t = torch.full((b,), t_index, device=device, dtype=torch.long)
    eps_theta = model(x, t)

    beta_t = betas[t_index]
    sqrt_one_minus_alpha_bar_t = sqrt_one_minus_alphas_cumprod[t_index]
    sqrt_recip_alpha_t = sqrt_recip_alphas[t_index]

    model_mean = sqrt_recip_alpha_t * (x - beta_t / sqrt_one_minus_alpha_bar_t * eps_theta)

    if t_index == 0:
        return model_mean
    else:
        noise = torch.randn_like(x)
        var = posterior_variance[t_index]
        return model_mean + torch.sqrt(var) * noise

@torch.no_grad()
def p_sample_loop(model, shape):
    model.eval()
    img = torch.randn(shape, device=device)
    for t_index in reversed(range(T)):
        img = p_sample(model, img, t_index)
    return img


for epoch in range(1, EPOCHS+1):
    model.train()
    epoch_loss = 0.0
    pbar = tqdm(trainloader, desc=f"Diffusion Epoch {epoch}/{EPOCHS}", unit="batch")
    last_real_batch = None

    for x0, _ in pbar:
        x0 = x0.to(device)

        loss = diffusion_loss(model, x0)
        optimizer.zero_grad(set_to_none=True)
        loss.backward()

        torch.nn.utils.clip_grad_norm_(model.parameters(), 1.0)

        optimizer.step()
        ema.update()

        epoch_loss += loss.item()
        last_real_batch = x0
        pbar.set_postfix(loss=f"{loss.item():.4f}", lr=f"{optimizer.param_groups[0]['lr']:.6f}")

    scheduler.step()
    avg_loss = epoch_loss / len(trainloader)
    print(f"Epoch {epoch} | loss={avg_loss:.4f}")

    if epoch % 50 == 0 or epoch == EPOCHS:
        ema.apply_shadow()

        with torch.no_grad():
            samples = p_sample_loop(model, (64, 3, 32, 32))
            samples = denorm(samples).cpu()
            reals = denorm(last_real_batch[:64].cpu())

            grid_real = make_grid(reals, nrow=8)
            grid_fake = make_grid(samples, nrow=8)
            combo = torch.cat([grid_real, grid_fake], dim=1)
            save_image(combo, os.path.join(OUT_DIR, f"real_vs_diffusion_epoch_{epoch:03d}.png"))

        ckpt = {
            "epoch": epoch,
            "model": model.state_dict(),
            "ema": ema.shadow,
            "optimizer": optimizer.state_dict(),
            "T": T,
        }
        torch.save(ckpt, os.path.join(OUT_DIR, f"diffusion_epoch_{epoch:03d}.pth"))

        ema.restore()

print("Training done. Checkpoints and grids saved in:", OUT_DIR)


# -------------------------
# EXPORT 10K SAMPLES (with EMA)
# -------------------------

from pathlib import Path

ckpt_path = os.path.join(OUT_DIR, f"diffusion_epoch_{EPOCHS:03d}.pth")
ckpt = torch.load(ckpt_path, map_location=device)

model = UNet(img_ch=3, base_channels=128, time_dim=256, dropout=0.1).to(device)
ema_state = ckpt.get("ema", ckpt["model"])

if isinstance(ema_state, dict):
    sample_keys = list(ema_state.keys())[:5] if len(ema_state) >= 5 else list(ema_state.keys())
    if sample_keys and all(k in model.state_dict() for k in sample_keys):
        model.load_state_dict(ema_state)
    else:
        ema_model = EMA(model, decay=0.9999)
        ema_model.shadow = ema_state
        ema_model.apply_shadow()
else:
    model.load_state_dict(ema_state)

SAMPLES_DIR = Path(OUT_DIR) / "samples_10k"
SAMPLES_DIR.mkdir(parents=True, exist_ok=True)

model.eval()
total = 10_000
bs = 100
saved = 0

print(f"Generating {total} samples...")
with torch.no_grad():
    while saved < total:
        cur = min(bs, total - saved)
        samples = p_sample_loop(model, (cur, 3, 32, 32))
        samples = denorm(samples).cpu()
        for i in range(cur):
            save_image(samples[i], SAMPLES_DIR / f"{saved + i:05d}.png")
        saved += cur
        if saved % 1000 == 0:
            print(f"Saved {saved}/{total} samples...")

print(f"Saved {saved} diffusion samples to {SAMPLES_DIR}")


# -------------------------
# FID, IS, KID
# -------------------------

!pip -q install "torch-fidelity>=0.3.0"

from torch_fidelity import calculate_metrics

EXPORT_DIR = str(SAMPLES_DIR)
print("Using diffusion samples from:", EXPORT_DIR)

orig_torch_load = torch.load

def _compat_load(*args, **kwargs):
    kwargs.setdefault("weights_only", False)
    return orig_torch_load(*args, **kwargs)

torch.load = _compat_load

try:
    print("\nCalculating FID and KID...")
    metrics_fid = calculate_metrics(
        input1=EXPORT_DIR,
        input2="cifar10-train",
        fid=True,
        kid=True,
        isc=False,
        cuda=(device == "cuda"),
        verbose=False,
    )

    print("Calculating Inception Score...")
    metrics_is = calculate_metrics(
        input1=EXPORT_DIR,
        fid=False,
        kid=False,
        isc=True,
        cuda=(device == "cuda"),
        verbose=False,
    )
finally:
    torch.load = orig_torch_load

fid  = metrics_fid.get("frechet_inception_distance", None)
kidm = metrics_fid.get("kernel_inception_distance_mean", metrics_fid.get("kid_mean", None))
kids = metrics_fid.get("kernel_inception_distance_std",  metrics_fid.get("kid_std",  None))

is_m = (metrics_is.get("inception_score_mean")
        or metrics_is.get("isc_mean")
        or metrics_is.get("inception_score"))
is_s = metrics_is.get("inception_score_std", metrics_is.get("isc_std", None))

print("\n" + "="*50)
print("=== IMPROVED DIFFUSION METRICS ===")
print("="*50)
print(f"FID : {fid:.2f}" if fid is not None else "FID : None")

if is_m is None:
    print("IS  : Not returned")
else:
    if is_s is not None:
        print(f"IS  : {is_m:.2f} ± {is_s:.2f}")
    else:
        print(f"IS  : {is_m:.2f}")

if kidm is None:
    print("KID : Not returned")
else:
    if kids is not None:
        print(f"KID : {kidm:.6f} ± {kids:.6f}")
    else:
        print(f"KID : {kidm:.6f}")

print("="*50)

with open(os.path.join(OUT_DIR, "metrics.txt"), "w") as f:
    f.write(f"FID: {fid}\n")
    f.write(f"IS_mean: {is_m}\n")
    f.write(f"IS_std: {is_s}\n")
    f.write(f"KID_mean: {kidm}\n")
    f.write(f"KID_std: {kids}\n")

print("\nSaved metrics to:", os.path.join(OUT_DIR, "metrics.txt"))


# -------------------------
# HELPER: GENERATE FROM CHECKPOINT LATER
# -------------------------

def load_diffusion_and_sample(ckpt_name="diffusion_epoch_500.pth",
                              n_samples=64, nrow=8,
                              out_name="diffusion_generated_grid.png"):
    """
    Load a saved diffusion checkpoint and generate a grid of images.
    """
    ckpt_path = os.path.join(OUT_DIR, ckpt_name)
    assert os.path.exists(ckpt_path), f"Checkpoint not found: {ckpt_path}"

    model = UNet(img_ch=3, base_channels=128, time_dim=256, dropout=0.1).to(device)
    ckpt = torch.load(ckpt_path, map_location=device)

    ema_state = ckpt.get("ema", ckpt["model"])
    if isinstance(ema_state, dict):
        sample_keys = list(ema_state.keys())[:5] if len(ema_state) >= 5 else list(ema_state.keys())
        if sample_keys and all(k in model.state_dict() for k in sample_keys):
            model.load_state_dict(ema_state)
        else:
            ema_model = EMA(model, decay=0.9999)
            ema_model.shadow = ema_state
            ema_model.apply_shadow()
    else:
        model.load_state_dict(ema_state)

    model.eval()

    with torch.no_grad():
        samples = p_sample_loop(model, (n_samples, 3, 32, 32))
        samples = denorm(samples).cpu()

    grid = make_grid(samples, nrow=nrow)
    out_path = os.path.join(OUT_DIR, out_name)
    save_image(grid, out_path)
    print("Saved new generated grid to:", out_path)

print("\n✅ All done! Your improved diffusion model is ready.")

GPU 0: NVIDIA A100-SXM4-40GB (UUID: GPU-29cddfd2-c2c2-cad2-0513-e7e669543a90)
Mounted at /content/drive
✅ Drive mounted. Saving to: /content/drive/MyDrive/diffusion_cifar10_runs
Device: cuda
OUT_DIR: /content/drive/MyDrive/diffusion_cifar10_runs
Train batches: 781


Diffusion Epoch 1/500:   0%|          | 0/781 [00:00<?, ?batch/s]

Epoch 1 | loss=0.1078


Diffusion Epoch 2/500:   0%|          | 0/781 [00:00<?, ?batch/s]

Epoch 2 | loss=0.0671


...

Epoch 499 | loss=0.0518


Diffusion Epoch 500/500:   0%|          | 0/781 [00:00<?, ?batch/s]

Epoch 500 | loss=0.0521
Training done. Checkpoints and grids saved in: /content/drive/MyDrive/diffusion_cifar10_runs
Generating 10000 samples...
Saved 1000/10000 samples...
Saved 2000/10000 samples...
Saved 3000/10000 samples...
Saved 4000/10000 samples...
Saved 5000/10000 samples...
Saved 6000/10000 samples...
Saved 7000/10000 samples...
Saved 8000/10000 samples...
Saved 9000/10000 samples...
Saved 10000/10000 samples...
Saved 10000 diffusion samples to /content/drive/MyDrive/diffusion_cifar10_runs/samples_10k
Using diffusion samples from: /content/drive/MyDrive/diffusion_cifar10_runs/samples_10k

Calculating FID and KID...


Downloading: "https://github.com/toshas/torch-fidelity/releases/download/v0.2.0/weights-inception-2015-12-05-6726825d.pth" to /root/.cache/torch/hub/checkpoints/weights-inception-2015-12-05-6726825d.pth
100%|██████████| 91.2M/91.2M [00:00<00:00, 179MB/s]
/usr/local/lib/python3.12/dist-packages/torch_fidelity/datasets.py:16: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  img = torch.ByteTensor(torch.ByteStorage.from_buffer(img.tobytes())).view(height, width, 3)
100%|██████████| 170M/170M [00:01<00:00, 100MB/s]


Calculating Inception Score...

=== IMPROVED DIFFUSION METRICS ===
FID : 11.03
IS  : 8.58 ± 0.20
KID : 0.004331 ± 0.000750

Saved metrics to: /content/drive/MyDrive/diffusion_cifar10_runs/metrics.txt

✅ All done! Your improved diffusion model is ready.
